In [138]:
import pandas as pd
import numpy as np
import random as rnd

import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline
#%matplotlib widget

from sklearn import preprocessing
import xgboost as xgb

import warnings
warnings.filterwarnings('ignore')

In [139]:
pd.set_option('display.max_columns', 17000)
pd.set_option('display.max_row', 17000)

In [140]:
df = pd.read_csv("D:\Python\Zindi\Flood\Train.csv", sep=",", index_col='Square_ID')

In [141]:
train = df.drop(['precip 2019-01-20 - 2019-01-27', 'precip 2019-01-27 - 2019-02-03',
 'precip 2019-02-03 - 2019-02-10', 'precip 2019-02-10 - 2019-02-17',
 'precip 2019-02-17 - 2019-02-24', 'precip 2019-02-24 - 2019-03-03',
 'precip 2019-03-03 - 2019-03-10', 'precip 2019-03-10 - 2019-03-17',
 'precip 2019-03-17 - 2019-03-24', 'precip 2019-03-24 - 2019-03-31',
 'precip 2019-03-31 - 2019-04-07', 'precip 2019-04-07 - 2019-04-14',
 'precip 2019-04-14 - 2019-04-21', 'precip 2019-04-21 - 2019-04-28',
 'precip 2019-04-28 - 2019-05-05', 'precip 2019-05-05 - 2019-05-12',
 'precip 2019-05-12 - 2019-05-19'], axis=1)

In [142]:
X_fulltest = df.drop(['precip 2014-11-16 - 2014-11-23',
 'precip 2014-11-23 - 2014-11-30', 'precip 2014-11-30 - 2014-12-07',
 'precip 2014-12-07 - 2014-12-14', 'precip 2014-12-14 - 2014-12-21',
 'precip 2014-12-21 - 2014-12-28', 'precip 2014-12-28 - 2015-01-04',
 'precip 2015-01-04 - 2015-01-11', 'precip 2015-01-11 - 2015-01-18',
 'precip 2015-01-18 - 2015-01-25', 'precip 2015-01-25 - 2015-02-01',
 'precip 2015-02-01 - 2015-02-08', 'precip 2015-02-08 - 2015-02-15',
 'precip 2015-02-15 - 2015-02-22', 'precip 2015-02-22 - 2015-03-01',
 'precip 2015-03-01 - 2015-03-08', 'precip 2015-03-08 - 2015-03-15'], axis=1)

Feature generating

In [144]:
Train_stat = train.drop (['X', 'Y', 'target_2015', 'elevation', 'LC_Type1_mode' ], axis=1)

In [145]:
Train_feature = Train_stat.copy()

In [146]:
Train_feature['Mean'] = Train_stat.mean(axis=1)
Train_feature['Median'] = Train_stat.median(axis=1)
from scipy.stats import norm
from scipy import stats
Train_feature['Skew'] = Train_stat.skew(axis=1)
Train_feature['Kurtosis'] = Train_stat.kurtosis(axis=1)
Train_feature['Var'] = Train_stat.var(axis=1)
Train_feature['Max'] = Train_stat.max(axis=1)
Train_feature['Min'] = Train_stat.min(axis=1)
Train_feature['Sum'] = Train_stat.sum(axis=1)

In [147]:
from io import StringIO
import pandas as pd
import scipy.stats
df = Train_stat
axisvalues=list(range(1,len(df.columns)+1))

def calc_slope(row):
    a = scipy.stats.linregress(row, y=axisvalues)
    return pd.Series(a._asdict())

Train_feature = Train_feature.join(Train_stat.apply(calc_slope,axis=1))

In [148]:
trainfull  = Train_feature.drop(['precip 2014-11-16 - 2014-11-23',
 'precip 2014-11-23 - 2014-11-30', 'precip 2014-11-30 - 2014-12-07',
 'precip 2014-12-07 - 2014-12-14', 'precip 2014-12-14 - 2014-12-21',
 'precip 2014-12-21 - 2014-12-28', 'precip 2014-12-28 - 2015-01-04',
 'precip 2015-01-04 - 2015-01-11', 'precip 2015-01-11 - 2015-01-18',
 'precip 2015-01-18 - 2015-01-25', 'precip 2015-01-25 - 2015-02-01',
 'precip 2015-02-01 - 2015-02-08', 'precip 2015-02-08 - 2015-02-15',
 'precip 2015-02-15 - 2015-02-22', 'precip 2015-02-22 - 2015-03-01',
 'precip 2015-03-01 - 2015-03-08', 'precip 2015-03-08 - 2015-03-15'], axis=1)

In [149]:
trainfull1 = train.merge(trainfull, how='left', left_index=True, right_index=True)

In [150]:
trainfull1  = trainfull1.drop(['precip 2014-11-16 - 2014-11-23',
 'precip 2014-11-23 - 2014-11-30', 'precip 2014-11-30 - 2014-12-07',
 'precip 2014-12-07 - 2014-12-14', 'precip 2014-12-14 - 2014-12-21',
 'precip 2014-12-21 - 2014-12-28', 'precip 2014-12-28 - 2015-01-04',
 'precip 2015-01-04 - 2015-01-11', 'precip 2015-01-11 - 2015-01-18',
 'precip 2015-01-18 - 2015-01-25', 'precip 2015-01-25 - 2015-02-01',
 'precip 2015-02-01 - 2015-02-08', 'precip 2015-02-08 - 2015-02-15',
 'precip 2015-02-15 - 2015-02-22', 'precip 2015-02-22 - 2015-03-01',
 'precip 2015-03-01 - 2015-03-08', 'precip 2015-03-08 - 2015-03-15'], axis=1)

Geofeaturing

In [151]:

#xy_scaler = preprocessing.StandardScaler () xy scaler.fit (trainfull1 [["X", "Y"]])
#trainfull1 [["X", "Y"]] = xy_scaler.transform (trainfull1 [["X", "Y"]])

trainfull1['arctan2'] = np.arctan2(trainfull1['Y'], trainfull1['X'])
trainfull1['radial_r'] = np.sqrt( np.power(trainfull1['Y'],2) + np.power(trainfull1['X'],2))

trainfull1['rot45X'] = .707* trainfull1['Y'] + .707* trainfull1['X'] 
trainfull1['rot45Y'] = .707* trainfull1['Y'] - .707* trainfull1['X']

trainfull1['rot30X'] = (1.732/2)* trainfull1['X'] + (1./2)* trainfull1['Y'] 
trainfull1['rot30Y'] = (1.732/2)* trainfull1['Y'] - (1./2)* trainfull1['X']

trainfull1['rot60X'] = (1./2)* trainfull1['X'] + (1.732/2)* trainfull1['Y'] 
trainfull1['rot60Y'] = (1./2)* trainfull1['Y'] - (1.732/2)* trainfull1['X']




#trainfull1['rot_45_x'] = (0.707 * trainfull1['X']) + (0.707 * trainfull1['Y'])
#trainfull1['rot_45_y'] = (0.707 * trainfull1['Y']) + (0.707 * trainfull1['X'])
#trainfull1['rot_30_x'] = (0.866 * trainfull1['X']) + (0.5 * trainfull1['Y'])
#trainfull1['rot_30_y'] = (0.866 * trainfull1['Y']) + (0.5 * trainfull1['X'])

In [152]:
from sklearn.decomposition import PCA
data = trainfull1
coordinates = data[['X','Y']].values
pca_obj = PCA().fit(coordinates)
trainfull1['pca_x'] = pca_obj.transform(data[['X', 'Y']])[:,0]
trainfull1['pca_y'] = pca_obj.transform(data[['X','Y']])[:,1]

In [153]:
#base case Balantayer
from haversine import haversine
city_center_coordinates = (35.003815, -15.788289)

trainfull1['dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), city_center_coordinates), axis=1)

In [154]:
import pygeohash as gh
# создаем переменную - геохеш
trainfull1['geohash'] = trainfull1.apply(lambda x: gh.encode(x['X'], x['Y'], precision=6), axis=1) #лучший результат с 6 знаками


In [155]:
geohash_center = gh.encode(35.003815, -15.788289, precision=6)

# преобразовываем геохеш "центра" во множество
geohash_center_set = set(geohash_center)
# создаем переменную - количество совпадающих символов
# (учитываем повторяющиеся символы)
trainfull1['match'] = trainfull1['geohash'].apply(lambda x: sum([let1 == let2 for let1, let2 in zip(geohash_center, x)]))
# создаем переменную - количество совпадающих символов
# (не учитываем повторяющиеся символы)
trainfull1['match2'] = trainfull1['geohash'].apply(lambda x: len(set(x) & geohash_center_set))

In [165]:
# падает качество много шума
#from haversine import haversine
#Zomba_city_center_coordinates = (35.326827, -15.386321)
#Chikwawa_city_center_coordinates = (34.791215, -16.027131)
#Phalombe_city_center_coordinates = (35.648067, -15.806557)
#Nsanje_city_center_coordinates = (35.261946, -16.923236)
#Mangochi_city_center_coordinates = (35.260613, -14.480508)
#LakeChilwa_city_center_coordinates = (35.657501, -15.389474)
#LakeMalombe_city_center_coordinates = (35.244141, -14.666633)

#trainfull1['Zomba_dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), Zomba_city_center_coordinates), axis=1)
#trainfull1['Chikwawa_dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), Chikwawa_city_center_coordinates), axis=1)
#trainfull1['Phalombe_dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), Phalombe_city_center_coordinates), axis=1)
#trainfull1['Nsanje_dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), Nsanje_city_center_coordinates), axis=1)
#trainfull1['Mangochi_dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), Mangochi_city_center_coordinates), axis=1)
#trainfull1['LakeChilwa_dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), LakeChilwa_city_center_coordinates), axis=1)
#trainfull1['LakeMalombe_dist_center'] = trainfull1.apply(lambda row: haversine((row['X'], row['Y']), LakeMalombe_city_center_coordinates), axis=1)

In [166]:
#Расстояние до реки Шир ЮГ реки в виде отрезка падало качество на сабмите
#import math
#import numpy as np

#def shortest_distance(x1, y1, a, b, c):    
#    d = abs((a * x1 + b * y1 + c)) / (math.sqrt(a * a + b * b)) 
#    return d

#closest = []
#x = (34.745636, -15.878130)
#y = (35.149384, -16.545380)
#coef = np.polyfit(x, y, 1)
#A = coef[0]
#B = coef[1]
#C = A*x[0] + B*x[1]



#trainfull1['dist_river_Sheer_s'] = trainfull1.apply(lambda row: shortest_distance(row['X'], row['Y'], A, B, C), axis=1)

In [167]:
#Расстояние до реки Шир СЕВЕР реки в виде вектора
#import math
#import numpy as np

#def shortest_distance(x1, y1, a, b, c):    
#    d = abs((a * x1 + b * y1 + c)) / (math.sqrt(a * a + b * b)) 
#    return d

#closest = []
#x = (35.293579, -15.878130)
#y = (34.730530, -15.732779)
#coef = np.polyfit(x, y, 1)
#A = coef[0]
#B = coef[1]
#C = A*x[0] + B*x[1]

#trainfull1['dist_river_Sheer_n'] = trainfull1.apply(lambda row: shortest_distance(row['X'], row['Y'], A, B, C), axis=1)

In [168]:
#Расстояние до реки RUO реки в виде вектора
#import math
#import numpy as np

#def shortest_distance(x1, y1, a, b, c):    
#    d = abs((a * x1 + b * y1 + c)) / (math.sqrt(a * a + b * b)) 
#    return d

#closest = []
#x = (35.620422, -16.114431)
#y = (35.191956, -16.445305)
#coef = np.polyfit(x, y, 1)
#A = coef[0]
#B = coef[1]
#C = A*x[0] + B*x[1]

#trainfull1['dist_river_Ruo'] = trainfull1.apply(lambda row: shortest_distance(row['X'], row['Y'], A, B, C), axis=1)

In [37]:
#trainfull1  = trainfull1.drop(['X','Y'], axis=1) падает качество коородинаты оставим

# Эксперименты с  моделями с отложеной выборокой на тест - градиентный бустинг

In [29]:
# разбиваем данные на обучающие и тестовые: получаем обучающий
# массив признаков, тестовый массив признаков, обучающий массив
# меток, тестовый массив меток
import os
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(trainfull1.drop('target_2015', axis=1), trainfull1['target_2015'], test_size=0.3,  random_state=42)


In [30]:
# Label Encoding категориальных признаков. 
# Mы можем выполнить Label Encoding как до так и после разбиения на обучающую и тестовую выборки (до перекрестной проверки).

for f in X_train.columns:
    if X_train[f].dtype=='object' or X_test[f].dtype=='object': 
        lbl = preprocessing.LabelEncoder()
        lbl.fit(list(X_train[f].values) + list(X_test[f].values))
        X_train[f] = lbl.transform(list(X_train[f].values))
        X_test[f] = lbl.transform(list(X_test[f].values))

In [31]:
clf = xgb.XGBRegressor(
    n_estimators=3800,
    max_depth=13,
    learning_rate=0.005, #eta = 0.005,
    subsample=0.9,
    colsample_bytree=0.4,
    random_state=2019,
    objective='reg:linear',
    #subsample = 0.3,
    tree_method='gpu_hist'  #обучимся на видюшке - скорость огонь минуты против часов
)



In [31]:
# єксперимент с гипероптом
clf = xgb.XGBRegressor(
    n_estimators=1600,
    max_depth=16,
    learning_rate=0.02, #eta = 0.005,
    subsample=0.75,
    colsample_bytree=0.4,
    #gamma = 0.75,
    #min_child_weight = 3.0,
    #reg_lambda = 1.4000000000000001,
    random_state=2019,
    objective='reg:linear',
    #alpha = 2.0,
    tree_method='gpu_hist'  #обучимся на видюшке - скорость огонь минуты против часов
)



In [32]:
%time clf.fit(X_train, y_train)

[12:30:35] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
Wall time: 5min 51s


XGBRegressor(base_score=0.5, booster='gbtree', colsample_bylevel=1,
             colsample_bynode=1, colsample_bytree=0.4, gamma=0,
             importance_type='gain', learning_rate=0.005, max_delta_step=0,
             max_depth=13, min_child_weight=1, missing=None, n_estimators=3800,
             n_jobs=1, nthread=None, objective='reg:linear', random_state=2019,
             reg_alpha=0, reg_lambda=1, scale_pos_weight=1, seed=None,
             silent=None, subsample=0.9, tree_method='gpu_hist', verbosity=1)

In [33]:
from sklearn.metrics import mean_squared_error
from math import sqrt
import math
print("RMSE: %.10f"
      % math.sqrt(np.mean((clf.predict(X_test) - y_test) ** 2)))

RMSE: 0.0855475151


Подбор гиперпараметров

In [53]:
from sklearn.metrics import mean_squared_error
import xgboost as xgb
from hyperopt import hp, fmin, tpe, STATUS_OK, Trials
import numpy as np
X = X_train
Xcv = X_test
y = y_train
ycv = y_test


def objective(space):
    print(space)
    clf = xgb.XGBRegressor(n_estimators =space[ 'n_estimators'],
                           colsample_bytree=space['colsample_bytree'],
                           learning_rate = space['learning_rate'],
                           max_depth = int(space['max_depth']),
                           #min_child_weight = space['min_child_weight'],
                           subsample = space['subsample'],
                           #gamma = space['gamma'], 
                           random_state=2019,
                           #reg_lambda = space['reg_lambda'],
                           tree_method='gpu_hist', 
                           #alpha = space['alpha'],
                           objective='reg:linear')
                            

    eval_set  = [( X, y), ( Xcv, ycv)]
    
    clf.fit(X, y, 
            eval_set=eval_set, eval_metric="rmse", 
            early_stopping_rounds=10, verbose=False)

    pred = clf.predict(Xcv)
    mse_scr = mean_squared_error(ycv, pred)
    print ("SCORE:", np.sqrt(mse_scr))
    #change the metric if you like
    return {'loss':mse_scr, 'status': STATUS_OK }


space ={'max_depth': hp.quniform("x_max_depth", 4, 16, 1),
        'n_estimators' : hp.choice('n_estimators', np.arange(1000, 4000, 100, dtype=int)),
        'learning_rate' : hp.quniform('learning_rate', 0.005, 0.3, 0.005),
        #'min_child_weight': hp.quniform ('x_min_child', 1, 10, 1),
        'subsample': hp.quniform('subsample', 0.6, 1.0, 0.05),
        #'gamma' : hp.quniform('gamma', 0.5, 1, 0.05),
        'colsample_bytree' : hp.quniform('colsample_bytree', 0.3, 1, 0.05),
        #'reg_lambda' : hp.quniform('lambda', 1, 2, 0.1),
        #'alpha' :  hp.quniform('alpha', 0, 10, 1),
        
    }


trials = Trials()
best = fmin(fn=objective,
            space=space,
            algo=tpe.suggest,
            max_evals=250,
            trials=trials)

print (best)

{'colsample_bytree': 0.8500000000000001, 'learning_rate': 0.12, 'max_depth': 11.0, 'n_estimators': 2800, 'subsample': 0.65}
[09:27:05] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                                                                 
0.08996369957676628                                                                                                    
{'colsample_bytree': 0.9500000000000001, 'learning_rate': 0.08, 'max_depth': 10.0, 'n_estimators': 1700, 'subsample': 0.6000000000000001}
[09:27:12] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                                                                 
0.08976083688146323                               

SCORE:                                                                                                                 
0.08550993909392321                                                                                                    
{'colsample_bytree': 0.35000000000000003, 'learning_rate': 0.03, 'max_depth': 14.0, 'n_estimators': 2400, 'subsample': 0.9}
[09:42:02] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                                                                 
0.08578845643176028                                                                                                    
{'colsample_bytree': 0.35000000000000003, 'learning_rate': 0.095, 'max_depth': 12.0, 'n_estimators': 2400, 'subsample': 1.0}
[09:43:09] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: re

[09:54:28] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                                                                 
0.08879793659191253                                                                                                    
{'colsample_bytree': 0.6000000000000001, 'learning_rate': 0.07, 'max_depth': 7.0, 'n_estimators': 3900, 'subsample': 1.0}
[09:55:18] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                                                                 
0.08917804408040715                                                                                                    
{'colsample_bytree': 0.9500000000000001, 'learning_rate': 0.02, 'max_d

0.09260576964779921                                                                                                    
{'colsample_bytree': 0.4, 'learning_rate': 0.01, 'max_depth': 9.0, 'n_estimators': 3000, 'subsample': 0.8}             
[10:26:36] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                                                                 
0.08632843040930324                                                                                                    
{'colsample_bytree': 0.45, 'learning_rate': 0.025, 'max_depth': 12.0, 'n_estimators': 1800, 'subsample': 0.9}          
[10:27:20] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                  

SCORE:                                                                                                                 
0.08586242037310349                                                                                                    
{'colsample_bytree': 0.5, 'learning_rate': 0.095, 'max_depth': 14.0, 'n_estimators': 2300, 'subsample': 1.0}           
[10:48:39] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
SCORE:                                                                                                                 
0.08934496248387791                                                                                                    
{'colsample_bytree': 0.35000000000000003, 'learning_rate': 0.07, 'max_depth': 16.0, 'n_estimators': 3700, 'subsample': 0.9}
[10:48:53] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:lin

KeyboardInterrupt: 

In [61]:
import catboost
from sklearn.model_selection import KFold
from catboost import Pool, CatBoostClassifier, CatBoostRegressor
from catboost import MetricVisualizer
import matplotlib
import seaborn as sns
%matplotlib inline #для статики
%matplotlib widget #для динамики

UsageError: unrecognized arguments: #для статики


In [59]:
#Базовый Catboost
model = CatBoostRegressor(
    eval_metric='RMSE',
    iterations=9000,  
    learning_rate=0.005, 
    depth = 9,
    random_seed=42,
    loss_function='RMSE',
    #random_strength= 0.1,
   # bagging_temperature=0.1,
    #l2_leaf_reg= 30, 
    use_best_model = True, 
    #logging_level='Silent'
    task_type="GPU"
)

In [60]:
model.fit(
      X_train, y_train, 
      eval_set=(X_test, y_test), 
      use_best_model=True,
      plot=True
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 0.2307036	test: 0.2217404	best: 0.2217404 (0)	total: 54.3ms	remaining: 8m 8s
1:	learn: 0.2300014	test: 0.2210654	best: 0.2210654 (1)	total: 108ms	remaining: 8m 7s
2:	learn: 0.2293030	test: 0.2203849	best: 0.2203849 (2)	total: 163ms	remaining: 8m 7s
3:	learn: 0.2286106	test: 0.2197196	best: 0.2197196 (3)	total: 214ms	remaining: 8m 1s
4:	learn: 0.2279301	test: 0.2190522	best: 0.2190522 (4)	total: 264ms	remaining: 7m 55s
5:	learn: 0.2272356	test: 0.2183845	best: 0.2183845 (5)	total: 317ms	remaining: 7m 55s
6:	learn: 0.2265445	test: 0.2177183	best: 0.2177183 (6)	total: 367ms	remaining: 7m 52s
7:	learn: 0.2258820	test: 0.2170609	best: 0.2170609 (7)	total: 416ms	remaining: 7m 47s
8:	learn: 0.2252173	test: 0.2164224	best: 0.2164224 (8)	total: 464ms	remaining: 7m 43s
9:	learn: 0.2245486	test: 0.2157769	best: 0.2157769 (9)	total: 516ms	remaining: 7m 43s
10:	learn: 0.2238831	test: 0.2151233	best: 0.2151233 (10)	total: 569ms	remaining: 7m 44s
11:	learn: 0.2232221	test: 0.2144803	best: 0

94:	learn: 0.1809107	test: 0.1741071	best: 0.1741071 (94)	total: 4.81s	remaining: 7m 30s
95:	learn: 0.1805344	test: 0.1737425	best: 0.1737425 (95)	total: 4.86s	remaining: 7m 31s
96:	learn: 0.1801334	test: 0.1733682	best: 0.1733682 (96)	total: 4.92s	remaining: 7m 32s
97:	learn: 0.1797589	test: 0.1730150	best: 0.1730150 (97)	total: 4.98s	remaining: 7m 32s
98:	learn: 0.1793887	test: 0.1726702	best: 0.1726702 (98)	total: 5.03s	remaining: 7m 32s
99:	learn: 0.1790337	test: 0.1723358	best: 0.1723358 (99)	total: 5.08s	remaining: 7m 32s
100:	learn: 0.1786677	test: 0.1719856	best: 0.1719856 (100)	total: 5.13s	remaining: 7m 32s
101:	learn: 0.1782936	test: 0.1716338	best: 0.1716338 (101)	total: 5.19s	remaining: 7m 32s
102:	learn: 0.1779197	test: 0.1712873	best: 0.1712873 (102)	total: 5.25s	remaining: 7m 33s
103:	learn: 0.1775685	test: 0.1709428	best: 0.1709428 (103)	total: 5.29s	remaining: 7m 32s
104:	learn: 0.1772084	test: 0.1705997	best: 0.1705997 (104)	total: 5.34s	remaining: 7m 32s
105:	learn:

189:	learn: 0.1534623	test: 0.1488018	best: 0.1488018 (189)	total: 9.64s	remaining: 7m 27s
190:	learn: 0.1532425	test: 0.1486101	best: 0.1486101 (190)	total: 9.69s	remaining: 7m 27s
191:	learn: 0.1530223	test: 0.1484246	best: 0.1484246 (191)	total: 9.74s	remaining: 7m 26s
192:	learn: 0.1528224	test: 0.1482361	best: 0.1482361 (192)	total: 9.79s	remaining: 7m 26s
193:	learn: 0.1526239	test: 0.1480515	best: 0.1480515 (193)	total: 9.85s	remaining: 7m 27s
194:	learn: 0.1524024	test: 0.1478555	best: 0.1478555 (194)	total: 9.9s	remaining: 7m 26s
195:	learn: 0.1521876	test: 0.1476679	best: 0.1476679 (195)	total: 9.94s	remaining: 7m 26s
196:	learn: 0.1519721	test: 0.1474737	best: 0.1474737 (196)	total: 9.98s	remaining: 7m 26s
197:	learn: 0.1517918	test: 0.1473149	best: 0.1473149 (197)	total: 10s	remaining: 7m 25s
198:	learn: 0.1515832	test: 0.1471294	best: 0.1471294 (198)	total: 10.1s	remaining: 7m 25s
199:	learn: 0.1513902	test: 0.1469567	best: 0.1469567 (199)	total: 10.1s	remaining: 7m 25s
20

282:	learn: 0.1383586	test: 0.1358580	best: 0.1358580 (282)	total: 14.3s	remaining: 7m 21s
283:	learn: 0.1382553	test: 0.1357706	best: 0.1357706 (283)	total: 14.4s	remaining: 7m 21s
284:	learn: 0.1381364	test: 0.1356771	best: 0.1356771 (284)	total: 14.5s	remaining: 7m 22s
285:	learn: 0.1379976	test: 0.1355769	best: 0.1355769 (285)	total: 14.5s	remaining: 7m 22s
286:	learn: 0.1378848	test: 0.1354820	best: 0.1354820 (286)	total: 14.6s	remaining: 7m 22s
287:	learn: 0.1377508	test: 0.1353779	best: 0.1353779 (287)	total: 14.6s	remaining: 7m 22s
288:	learn: 0.1376426	test: 0.1352923	best: 0.1352923 (288)	total: 14.7s	remaining: 7m 22s
289:	learn: 0.1375393	test: 0.1352101	best: 0.1352101 (289)	total: 14.7s	remaining: 7m 22s
290:	learn: 0.1373924	test: 0.1350953	best: 0.1350953 (290)	total: 14.8s	remaining: 7m 22s
291:	learn: 0.1372525	test: 0.1349898	best: 0.1349898 (291)	total: 14.8s	remaining: 7m 22s
292:	learn: 0.1371166	test: 0.1348922	best: 0.1348922 (292)	total: 14.9s	remaining: 7m 22s

...

8551:	learn: 0.0817532	test: 0.0973507	best: 0.0973507 (8551)	total: 5m 41s	remaining: 17.9s
8552:	learn: 0.0817531	test: 0.0973510	best: 0.0973507 (8551)	total: 5m 41s	remaining: 17.8s
8553:	learn: 0.0817525	test: 0.0973492	best: 0.0973492 (8553)	total: 5m 41s	remaining: 17.8s
8554:	learn: 0.0817525	test: 0.0973492	best: 0.0973492 (8553)	total: 5m 41s	remaining: 17.8s
8555:	learn: 0.0817517	test: 0.0973492	best: 0.0973492 (8555)	total: 5m 41s	remaining: 17.7s
8556:	learn: 0.0817517	test: 0.0973492	best: 0.0973492 (8556)	total: 5m 41s	remaining: 17.7s
8557:	learn: 0.0817517	test: 0.0973492	best: 0.0973492 (8556)	total: 5m 41s	remaining: 17.6s
8558:	learn: 0.0817517	test: 0.0973492	best: 0.0973492 (8556)	total: 5m 41s	remaining: 17.6s
8559:	learn: 0.0817508	test: 0.0973494	best: 0.0973492 (8556)	total: 5m 41s	remaining: 17.6s
8560:	learn: 0.0817488	test: 0.0973484	best: 0.0973484 (8560)	total: 5m 41s	remaining: 17.5s
8561:	learn: 0.0817487	test: 0.0973484	best: 0.0973484 (8560)	total: 5

8642:	learn: 0.0816760	test: 0.0973203	best: 0.0973203 (8642)	total: 5m 44s	remaining: 14.2s
8643:	learn: 0.0816722	test: 0.0973183	best: 0.0973183 (8643)	total: 5m 44s	remaining: 14.2s
8644:	learn: 0.0816715	test: 0.0973185	best: 0.0973183 (8643)	total: 5m 44s	remaining: 14.2s
8645:	learn: 0.0816715	test: 0.0973185	best: 0.0973183 (8643)	total: 5m 44s	remaining: 14.1s
8646:	learn: 0.0816712	test: 0.0973184	best: 0.0973183 (8643)	total: 5m 44s	remaining: 14.1s
8647:	learn: 0.0816712	test: 0.0973184	best: 0.0973183 (8643)	total: 5m 44s	remaining: 14s
8648:	learn: 0.0816681	test: 0.0973169	best: 0.0973169 (8648)	total: 5m 44s	remaining: 14s
8649:	learn: 0.0816681	test: 0.0973169	best: 0.0973169 (8648)	total: 5m 44s	remaining: 13.9s
8650:	learn: 0.0816679	test: 0.0973170	best: 0.0973169 (8648)	total: 5m 44s	remaining: 13.9s
8651:	learn: 0.0816678	test: 0.0973171	best: 0.0973169 (8648)	total: 5m 44s	remaining: 13.9s
8652:	learn: 0.0816677	test: 0.0973171	best: 0.0973169 (8648)	total: 5m 44

8735:	learn: 0.0815758	test: 0.0972706	best: 0.0972706 (8735)	total: 5m 48s	remaining: 10.5s
8736:	learn: 0.0815758	test: 0.0972706	best: 0.0972706 (8736)	total: 5m 48s	remaining: 10.5s
8737:	learn: 0.0815758	test: 0.0972706	best: 0.0972706 (8736)	total: 5m 48s	remaining: 10.4s
8738:	learn: 0.0815757	test: 0.0972706	best: 0.0972706 (8738)	total: 5m 48s	remaining: 10.4s
8739:	learn: 0.0815721	test: 0.0972687	best: 0.0972687 (8739)	total: 5m 48s	remaining: 10.4s
8740:	learn: 0.0815721	test: 0.0972686	best: 0.0972686 (8740)	total: 5m 48s	remaining: 10.3s
8741:	learn: 0.0815721	test: 0.0972686	best: 0.0972686 (8740)	total: 5m 48s	remaining: 10.3s
8742:	learn: 0.0815721	test: 0.0972686	best: 0.0972686 (8740)	total: 5m 48s	remaining: 10.2s
8743:	learn: 0.0815700	test: 0.0972688	best: 0.0972686 (8740)	total: 5m 48s	remaining: 10.2s
8744:	learn: 0.0815697	test: 0.0972687	best: 0.0972686 (8740)	total: 5m 48s	remaining: 10.2s
8745:	learn: 0.0815672	test: 0.0972681	best: 0.0972681 (8745)	total: 5

8824:	learn: 0.0814583	test: 0.0972367	best: 0.0972367 (8824)	total: 5m 51s	remaining: 6.97s
8825:	learn: 0.0814549	test: 0.0972370	best: 0.0972367 (8824)	total: 5m 51s	remaining: 6.93s
8826:	learn: 0.0814549	test: 0.0972371	best: 0.0972367 (8824)	total: 5m 51s	remaining: 6.89s
8827:	learn: 0.0814548	test: 0.0972371	best: 0.0972367 (8824)	total: 5m 51s	remaining: 6.85s
8828:	learn: 0.0814505	test: 0.0972358	best: 0.0972358 (8828)	total: 5m 51s	remaining: 6.81s
8829:	learn: 0.0814493	test: 0.0972352	best: 0.0972352 (8829)	total: 5m 51s	remaining: 6.77s
8830:	learn: 0.0814492	test: 0.0972351	best: 0.0972351 (8830)	total: 5m 51s	remaining: 6.73s
8831:	learn: 0.0814492	test: 0.0972351	best: 0.0972351 (8831)	total: 5m 51s	remaining: 6.69s
8832:	learn: 0.0814492	test: 0.0972351	best: 0.0972351 (8832)	total: 5m 51s	remaining: 6.65s
8833:	learn: 0.0814491	test: 0.0972351	best: 0.0972351 (8833)	total: 5m 51s	remaining: 6.61s
8834:	learn: 0.0814491	test: 0.0972351	best: 0.0972351 (8833)	total: 5

8915:	learn: 0.0813532	test: 0.0971916	best: 0.0971916 (8913)	total: 5m 54s	remaining: 3.34s
8916:	learn: 0.0813531	test: 0.0971915	best: 0.0971915 (8916)	total: 5m 54s	remaining: 3.3s
8917:	learn: 0.0813515	test: 0.0971912	best: 0.0971912 (8917)	total: 5m 54s	remaining: 3.26s
8918:	learn: 0.0813515	test: 0.0971912	best: 0.0971912 (8917)	total: 5m 54s	remaining: 3.22s
8919:	learn: 0.0813515	test: 0.0971913	best: 0.0971912 (8917)	total: 5m 54s	remaining: 3.18s
8920:	learn: 0.0813515	test: 0.0971912	best: 0.0971912 (8917)	total: 5m 54s	remaining: 3.14s
8921:	learn: 0.0813515	test: 0.0971912	best: 0.0971912 (8917)	total: 5m 54s	remaining: 3.1s
8922:	learn: 0.0813515	test: 0.0971912	best: 0.0971912 (8917)	total: 5m 54s	remaining: 3.06s
8923:	learn: 0.0813496	test: 0.0971898	best: 0.0971898 (8923)	total: 5m 55s	remaining: 3.02s
8924:	learn: 0.0813496	test: 0.0971898	best: 0.0971898 (8923)	total: 5m 55s	remaining: 2.98s
8925:	learn: 0.0813492	test: 0.0971903	best: 0.0971898 (8923)	total: 5m 

In [61]:
print("RMSE: %.10f"
      % math.sqrt(np.mean((model.predict(X_test) - y_test) ** 2)))

RMSE: 0.0971457213


In [43]:
import lightgbm as lgb  
from lightgbm import LGBMClassifier
import pickle  
from sklearn.metrics import roc_auc_score  
params = {'num_leaves': 800,
          'min_child_weight': 0.03454472573214212,
          'feature_fraction': 0.3797454081646243,
          'bagging_fraction': 0.4181193142567742,
          'min_data_in_leaf': 200,
          'objective': 'regression',
          'max_depth': 17,
          'learning_rate': 0.005,
          "boosting_type": "gbdt",
          "bagging_seed": 11,
          "metric": 'rmse',
          "verbosity": -1,
          'reg_alpha': 0.3899927210061127,
          'reg_lambda': 0.6485237330340494,
          'random_state': 47
         }

In [80]:
import lightgbm as lgb  
from lightgbm import LGBMClassifier
import pickle  
params = {'objective': 'regression', 
                                       'num_leaves': 7, #was 3
                                       'learning_rate': 0.01, 
                                       'n_estimators' : 15000, #8000
                                       'max_bin' : 200, 
                                       'bagging_fraction': 0.75,
                                       'bagging_freq' : 5, 
                                       'bagging_seed' : 7,
                                       'feature_fraction' : 0.2, # 'was 0.2'
                                       'feature_fraction_seed' : 7,
                                       'verbose' : -1,
         }

In [81]:

trn_data = lgb.Dataset(X_train, label=y_train)

lgb_eval = lgb.Dataset(X_test, y_test, reference=trn_data) 
  
clf = lgb.train(params, trn_data, valid_sets=lgb_eval, num_boost_round=3000) 

[1]	valid_0's l2: 0.0488839
[2]	valid_0's l2: 0.0483016
[3]	valid_0's l2: 0.0478816
[4]	valid_0's l2: 0.0475565
[5]	valid_0's l2: 0.0471531
[6]	valid_0's l2: 0.0467786
[7]	valid_0's l2: 0.0465718
[8]	valid_0's l2: 0.0462112
[9]	valid_0's l2: 0.0459195
[10]	valid_0's l2: 0.045547
[11]	valid_0's l2: 0.0450149
[12]	valid_0's l2: 0.0446632
[13]	valid_0's l2: 0.0445051
[14]	valid_0's l2: 0.0443034
[15]	valid_0's l2: 0.0439251
[16]	valid_0's l2: 0.0436805
[17]	valid_0's l2: 0.0432059
[18]	valid_0's l2: 0.0428478
[19]	valid_0's l2: 0.0426908
[20]	valid_0's l2: 0.0424124
[21]	valid_0's l2: 0.041964
[22]	valid_0's l2: 0.0417831
[23]	valid_0's l2: 0.0414779
[24]	valid_0's l2: 0.0411766
[25]	valid_0's l2: 0.0407405
[26]	valid_0's l2: 0.0405917
[27]	valid_0's l2: 0.0404372
[28]	valid_0's l2: 0.0401694
[29]	valid_0's l2: 0.0398737
[30]	valid_0's l2: 0.0394804
[31]	valid_0's l2: 0.0390872
[32]	valid_0's l2: 0.0388079
[33]	valid_0's l2: 0.0385884
[34]	valid_0's l2: 0.0382114
[35]	valid_0's l2: 0.0379

[404]	valid_0's l2: 0.0175307
[405]	valid_0's l2: 0.0175285
[406]	valid_0's l2: 0.0175173
[407]	valid_0's l2: 0.0175018
[408]	valid_0's l2: 0.0174679
[409]	valid_0's l2: 0.0174645
[410]	valid_0's l2: 0.0174499
[411]	valid_0's l2: 0.0174402
[412]	valid_0's l2: 0.0174272
[413]	valid_0's l2: 0.0174185
[414]	valid_0's l2: 0.017404
[415]	valid_0's l2: 0.0173872
[416]	valid_0's l2: 0.0173688
[417]	valid_0's l2: 0.017362
[418]	valid_0's l2: 0.0173558
[419]	valid_0's l2: 0.0173431
[420]	valid_0's l2: 0.0173299
[421]	valid_0's l2: 0.017319
[422]	valid_0's l2: 0.0173095
[423]	valid_0's l2: 0.0172969
[424]	valid_0's l2: 0.0172872
[425]	valid_0's l2: 0.0172774
[426]	valid_0's l2: 0.0172734
[427]	valid_0's l2: 0.0172682
[428]	valid_0's l2: 0.0172636
[429]	valid_0's l2: 0.0172554
[430]	valid_0's l2: 0.0172376
[431]	valid_0's l2: 0.0172253
[432]	valid_0's l2: 0.0172074
[433]	valid_0's l2: 0.0171998
[434]	valid_0's l2: 0.0171977
[435]	valid_0's l2: 0.0171892
[436]	valid_0's l2: 0.0171819
[437]	valid_0

[855]	valid_0's l2: 0.0145769
[856]	valid_0's l2: 0.0145758
[857]	valid_0's l2: 0.0145727
[858]	valid_0's l2: 0.0145742
[859]	valid_0's l2: 0.0145728
[860]	valid_0's l2: 0.0145663
[861]	valid_0's l2: 0.0145632
[862]	valid_0's l2: 0.0145579
[863]	valid_0's l2: 0.0145555
[864]	valid_0's l2: 0.0145487
[865]	valid_0's l2: 0.0145454
[866]	valid_0's l2: 0.0145396
[867]	valid_0's l2: 0.0145362
[868]	valid_0's l2: 0.0145322
[869]	valid_0's l2: 0.0145268
[870]	valid_0's l2: 0.0145263
[871]	valid_0's l2: 0.0145231
[872]	valid_0's l2: 0.014519
[873]	valid_0's l2: 0.0145132
[874]	valid_0's l2: 0.014509
[875]	valid_0's l2: 0.0145063
[876]	valid_0's l2: 0.0145025
[877]	valid_0's l2: 0.0145008
[878]	valid_0's l2: 0.0144962
[879]	valid_0's l2: 0.0144922
[880]	valid_0's l2: 0.0144881
[881]	valid_0's l2: 0.0144846
[882]	valid_0's l2: 0.0144827
[883]	valid_0's l2: 0.0144792
[884]	valid_0's l2: 0.0144732
[885]	valid_0's l2: 0.0144676
[886]	valid_0's l2: 0.0144663
[887]	valid_0's l2: 0.0144651
[888]	valid_

[1322]	valid_0's l2: 0.0132025
[1323]	valid_0's l2: 0.0132025
[1324]	valid_0's l2: 0.0132003
[1325]	valid_0's l2: 0.0131999
[1326]	valid_0's l2: 0.0131983
[1327]	valid_0's l2: 0.013195
[1328]	valid_0's l2: 0.0131938
[1329]	valid_0's l2: 0.0131896
[1330]	valid_0's l2: 0.0131872
[1331]	valid_0's l2: 0.0131858
[1332]	valid_0's l2: 0.0131821
[1333]	valid_0's l2: 0.0131796
[1334]	valid_0's l2: 0.013177
[1335]	valid_0's l2: 0.013175
[1336]	valid_0's l2: 0.0131743
[1337]	valid_0's l2: 0.013174
[1338]	valid_0's l2: 0.0131726
[1339]	valid_0's l2: 0.0131713
[1340]	valid_0's l2: 0.0131699
[1341]	valid_0's l2: 0.0131688
[1342]	valid_0's l2: 0.0131664
[1343]	valid_0's l2: 0.0131628
[1344]	valid_0's l2: 0.0131614
[1345]	valid_0's l2: 0.0131583
[1346]	valid_0's l2: 0.0131559
[1347]	valid_0's l2: 0.0131539
[1348]	valid_0's l2: 0.0131506
[1349]	valid_0's l2: 0.013148
[1350]	valid_0's l2: 0.0131469
[1351]	valid_0's l2: 0.0131453
[1352]	valid_0's l2: 0.0131449
[1353]	valid_0's l2: 0.0131419
[1354]	valid_

[1789]	valid_0's l2: 0.0123611
[1790]	valid_0's l2: 0.0123611
[1791]	valid_0's l2: 0.0123612
[1792]	valid_0's l2: 0.0123604
[1793]	valid_0's l2: 0.0123599
[1794]	valid_0's l2: 0.0123591
[1795]	valid_0's l2: 0.0123598
[1796]	valid_0's l2: 0.0123602
[1797]	valid_0's l2: 0.0123582
[1798]	valid_0's l2: 0.012355
[1799]	valid_0's l2: 0.0123515
[1800]	valid_0's l2: 0.0123507
[1801]	valid_0's l2: 0.0123497
[1802]	valid_0's l2: 0.0123479
[1803]	valid_0's l2: 0.0123467
[1804]	valid_0's l2: 0.012345
[1805]	valid_0's l2: 0.0123449
[1806]	valid_0's l2: 0.0123425
[1807]	valid_0's l2: 0.0123426
[1808]	valid_0's l2: 0.0123402
[1809]	valid_0's l2: 0.0123397
[1810]	valid_0's l2: 0.0123403
[1811]	valid_0's l2: 0.0123396
[1812]	valid_0's l2: 0.0123385
[1813]	valid_0's l2: 0.0123366
[1814]	valid_0's l2: 0.012336
[1815]	valid_0's l2: 0.012335
[1816]	valid_0's l2: 0.0123346
[1817]	valid_0's l2: 0.0123343
[1818]	valid_0's l2: 0.0123333
[1819]	valid_0's l2: 0.0123316
[1820]	valid_0's l2: 0.0123301
[1821]	valid

...

[12761]	valid_0's l2: 0.00886734
[12762]	valid_0's l2: 0.0088673
[12763]	valid_0's l2: 0.008867
[12764]	valid_0's l2: 0.00886681
[12765]	valid_0's l2: 0.00886637
[12766]	valid_0's l2: 0.00886635
[12767]	valid_0's l2: 0.00886635
[12768]	valid_0's l2: 0.0088663
[12769]	valid_0's l2: 0.00886621
[12770]	valid_0's l2: 0.00886682
[12771]	valid_0's l2: 0.00886673
[12772]	valid_0's l2: 0.00886671
[12773]	valid_0's l2: 0.00886693
[12774]	valid_0's l2: 0.00886681
[12775]	valid_0's l2: 0.00886673
[12776]	valid_0's l2: 0.0088667
[12777]	valid_0's l2: 0.00886677
[12778]	valid_0's l2: 0.00886646
[12779]	valid_0's l2: 0.0088666
[12780]	valid_0's l2: 0.00886648
[12781]	valid_0's l2: 0.00886639
[12782]	valid_0's l2: 0.00886625
[12783]	valid_0's l2: 0.00886611
[12784]	valid_0's l2: 0.00886572
[12785]	valid_0's l2: 0.00886567
[12786]	valid_0's l2: 0.00886573
[12787]	valid_0's l2: 0.00886559
[12788]	valid_0's l2: 0.00886557
[12789]	valid_0's l2: 0.00886553
[12790]	valid_0's l2: 0.00886501
[12791]	valid_0'

[13217]	valid_0's l2: 0.0088255
[13218]	valid_0's l2: 0.00882521
[13219]	valid_0's l2: 0.00882515
[13220]	valid_0's l2: 0.00882502
[13221]	valid_0's l2: 0.00882484
[13222]	valid_0's l2: 0.00882437
[13223]	valid_0's l2: 0.00882412
[13224]	valid_0's l2: 0.00882376
[13225]	valid_0's l2: 0.00882376
[13226]	valid_0's l2: 0.00882374
[13227]	valid_0's l2: 0.00882376
[13228]	valid_0's l2: 0.00882324
[13229]	valid_0's l2: 0.00882305
[13230]	valid_0's l2: 0.00882277
[13231]	valid_0's l2: 0.00882276
[13232]	valid_0's l2: 0.00882309
[13233]	valid_0's l2: 0.00882286
[13234]	valid_0's l2: 0.00882221
[13235]	valid_0's l2: 0.00882202
[13236]	valid_0's l2: 0.0088222
[13237]	valid_0's l2: 0.00882165
[13238]	valid_0's l2: 0.00882157
[13239]	valid_0's l2: 0.00882102
[13240]	valid_0's l2: 0.00882083
[13241]	valid_0's l2: 0.00882103
[13242]	valid_0's l2: 0.00882098
[13243]	valid_0's l2: 0.00882099
[13244]	valid_0's l2: 0.00882097
[13245]	valid_0's l2: 0.00882105
[13246]	valid_0's l2: 0.00882094
[13247]	vali

[13661]	valid_0's l2: 0.0087924
[13662]	valid_0's l2: 0.00879257
[13663]	valid_0's l2: 0.0087923
[13664]	valid_0's l2: 0.0087925
[13665]	valid_0's l2: 0.00879257
[13666]	valid_0's l2: 0.00879215
[13667]	valid_0's l2: 0.00879197
[13668]	valid_0's l2: 0.00879249
[13669]	valid_0's l2: 0.00879259
[13670]	valid_0's l2: 0.0087923
[13671]	valid_0's l2: 0.00879207
[13672]	valid_0's l2: 0.00879182
[13673]	valid_0's l2: 0.00879173
[13674]	valid_0's l2: 0.0087915
[13675]	valid_0's l2: 0.00879151
[13676]	valid_0's l2: 0.00879166
[13677]	valid_0's l2: 0.00879161
[13678]	valid_0's l2: 0.00879136
[13679]	valid_0's l2: 0.00879139
[13680]	valid_0's l2: 0.00879127
[13681]	valid_0's l2: 0.00879135
[13682]	valid_0's l2: 0.00879127
[13683]	valid_0's l2: 0.00879105
[13684]	valid_0's l2: 0.00879095
[13685]	valid_0's l2: 0.00879094
[13686]	valid_0's l2: 0.00879056
[13687]	valid_0's l2: 0.00879019
[13688]	valid_0's l2: 0.0087902
[13689]	valid_0's l2: 0.00878957
[13690]	valid_0's l2: 0.00878954
[13691]	valid_0'

[14123]	valid_0's l2: 0.00876792
[14124]	valid_0's l2: 0.00876799
[14125]	valid_0's l2: 0.00876806
[14126]	valid_0's l2: 0.00876664
[14127]	valid_0's l2: 0.0087666
[14128]	valid_0's l2: 0.00876651
[14129]	valid_0's l2: 0.00876626
[14130]	valid_0's l2: 0.00876639
[14131]	valid_0's l2: 0.00876601
[14132]	valid_0's l2: 0.008766
[14133]	valid_0's l2: 0.00876601
[14134]	valid_0's l2: 0.00876603
[14135]	valid_0's l2: 0.00876599
[14136]	valid_0's l2: 0.00876553
[14137]	valid_0's l2: 0.00876532
[14138]	valid_0's l2: 0.00876562
[14139]	valid_0's l2: 0.00876552
[14140]	valid_0's l2: 0.00876568
[14141]	valid_0's l2: 0.00876566
[14142]	valid_0's l2: 0.00876568
[14143]	valid_0's l2: 0.00876557
[14144]	valid_0's l2: 0.00876549
[14145]	valid_0's l2: 0.00876565
[14146]	valid_0's l2: 0.0087657
[14147]	valid_0's l2: 0.00876542
[14148]	valid_0's l2: 0.00876568
[14149]	valid_0's l2: 0.00876537
[14150]	valid_0's l2: 0.00876545
[14151]	valid_0's l2: 0.00876519
[14152]	valid_0's l2: 0.00876523
[14153]	valid_

[14588]	valid_0's l2: 0.0087396
[14589]	valid_0's l2: 0.00873967
[14590]	valid_0's l2: 0.00874036
[14591]	valid_0's l2: 0.00874045
[14592]	valid_0's l2: 0.00874026
[14593]	valid_0's l2: 0.00874045
[14594]	valid_0's l2: 0.00874062
[14595]	valid_0's l2: 0.00874038
[14596]	valid_0's l2: 0.00874032
[14597]	valid_0's l2: 0.00874034
[14598]	valid_0's l2: 0.00874036
[14599]	valid_0's l2: 0.00874055
[14600]	valid_0's l2: 0.00874106
[14601]	valid_0's l2: 0.00874109
[14602]	valid_0's l2: 0.00874082
[14603]	valid_0's l2: 0.00874057
[14604]	valid_0's l2: 0.00874056
[14605]	valid_0's l2: 0.00874034
[14606]	valid_0's l2: 0.00874034
[14607]	valid_0's l2: 0.00873991
[14608]	valid_0's l2: 0.0087396
[14609]	valid_0's l2: 0.00873954
[14610]	valid_0's l2: 0.00873925
[14611]	valid_0's l2: 0.00873922
[14612]	valid_0's l2: 0.00873909
[14613]	valid_0's l2: 0.00873936
[14614]	valid_0's l2: 0.00873941
[14615]	valid_0's l2: 0.00873945
[14616]	valid_0's l2: 0.00873936
[14617]	valid_0's l2: 0.00873937
[14618]	vali

In [82]:
from math import sqrt
import math
print("RMSE: %.10f"
      % math.sqrt(np.mean((clf.predict(X_test) - y_test) ** 2)))

RMSE: 0.0933857515


In [93]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.datasets import make_regression
regr = RandomForestRegressor(max_depth=15, random_state=0)
regr.fit(X_train, y_train)
print("RMSE: %.10f"
      % math.sqrt(np.mean((regr.predict(X_test) - y_test) ** 2)))

RMSE: 0.0996756708


# Обучим на всем train сете предскажем на тесте и сформируем посылку на Zindi

In [156]:
Test_stat = X_fulltest.drop (['X', 'Y', 'target_2015', 'elevation', 'LC_Type1_mode'], axis=1)

In [157]:
Test_feature = Test_stat.copy()

In [158]:
Test_feature['Mean'] = Test_stat.mean(axis=1)
Test_feature['Median'] = Test_stat.median(axis=1)
from scipy.stats import norm
from scipy import stats
Test_feature['Skew'] = Test_stat.skew(axis=1)
Test_feature['Kurtosis'] = Train_stat.kurtosis(axis=1)
Test_feature['Var'] = Test_stat.var(axis=1)
Test_feature['Max'] = Test_stat.max(axis=1)
Test_feature['Min'] = Test_stat.min(axis=1)
Test_feature['Sum'] = Test_stat.sum(axis=1)

In [159]:
from io import StringIO
import pandas as pd
import scipy.stats
df = Test_stat
axisvalues=list(range(1,len(df.columns)+1))

def calc_slope(row):
    a = scipy.stats.linregress(row, y=axisvalues)
    return pd.Series(a._asdict())

Test_feature = Test_feature.join(Test_stat.apply(calc_slope,axis=1))

In [160]:
X_testsubm  = Test_feature.drop(['precip 2019-01-20 - 2019-01-27', 'precip 2019-01-27 - 2019-02-03',
 'precip 2019-02-03 - 2019-02-10', 'precip 2019-02-10 - 2019-02-17',
 'precip 2019-02-17 - 2019-02-24', 'precip 2019-02-24 - 2019-03-03',
 'precip 2019-03-03 - 2019-03-10', 'precip 2019-03-10 - 2019-03-17',
 'precip 2019-03-17 - 2019-03-24', 'precip 2019-03-24 - 2019-03-31',
 'precip 2019-03-31 - 2019-04-07', 'precip 2019-04-07 - 2019-04-14',
 'precip 2019-04-14 - 2019-04-21', 'precip 2019-04-21 - 2019-04-28',
 'precip 2019-04-28 - 2019-05-05', 'precip 2019-05-05 - 2019-05-12',
 'precip 2019-05-12 - 2019-05-19'], axis=1)

In [161]:
X_testsubm1 = X_fulltest.merge(X_testsubm, how='left', left_index=True, right_index=True)

In [162]:
X_testsubm1  = X_testsubm1.drop(['precip 2019-01-20 - 2019-01-27', 'precip 2019-01-27 - 2019-02-03',
 'precip 2019-02-03 - 2019-02-10', 'precip 2019-02-10 - 2019-02-17',
 'precip 2019-02-17 - 2019-02-24', 'precip 2019-02-24 - 2019-03-03',
 'precip 2019-03-03 - 2019-03-10', 'precip 2019-03-10 - 2019-03-17',
 'precip 2019-03-17 - 2019-03-24', 'precip 2019-03-24 - 2019-03-31',
 'precip 2019-03-31 - 2019-04-07', 'precip 2019-04-07 - 2019-04-14',
 'precip 2019-04-14 - 2019-04-21', 'precip 2019-04-21 - 2019-04-28',
 'precip 2019-04-28 - 2019-05-05', 'precip 2019-05-05 - 2019-05-12',
 'precip 2019-05-12 - 2019-05-19'], axis=1)

In [163]:
#xy_scaler = preprocessing.StandardScaler () xy scaler.fit (trainfull1 [["X", "Y"]])
#trainfull1 [["X", "Y"]] = xy_scaler.transform (trainfull1 [["X", "Y"]])

X_testsubm1['arctan2'] = np.arctan2(X_testsubm1['Y'], X_testsubm1['X'])
X_testsubm1['radial_r'] = np.sqrt( np.power(X_testsubm1['Y'],2) + np.power(X_testsubm1['X'],2))

X_testsubm1['rot45X'] = .707* X_testsubm1['Y'] + .707* X_testsubm1['X'] 
X_testsubm1['rot45Y'] = .707* X_testsubm1['Y'] - .707* X_testsubm1['X']

X_testsubm1['rot30X'] = (1.732/2)* X_testsubm1['X'] + (1./2)* X_testsubm1['Y'] 
X_testsubm1['rot30Y'] = (1.732/2)* X_testsubm1['Y'] - (1./2)* X_testsubm1['X']

X_testsubm1['rot60X'] = (1./2)* X_testsubm1['X'] + (1.732/2)* X_testsubm1['Y'] 
X_testsubm1['rot60Y'] = (1./2)* X_testsubm1['Y'] - (1.732/2)* X_testsubm1['X']

#X_testsubm1['rot_45_x'] = (0.707 * X_testsubm1['X']) + (0.707 * X_testsubm1['Y'])
#X_testsubm1['rot_45_y'] = (0.707 * X_testsubm1['Y']) + (0.707 * X_testsubm1['X'])
#X_testsubm1['rot_30_x'] = (0.866 * X_testsubm1['X']) + (0.5 * X_testsubm1['Y'])
#X_testsubm1['rot_30_y'] = (0.866 * X_testsubm1['Y']) + (0.5 * X_testsubm1['X'])

In [164]:
from sklearn.decomposition import PCA
data = X_testsubm1
coordinates = data[['X','Y']].values
pca_obj = PCA().fit(coordinates)
X_testsubm1['pca_x'] = pca_obj.transform(data[['X', 'Y']])[:,0]
X_testsubm1['pca_y'] = pca_obj.transform(data[['X','Y']])[:,1]

In [165]:
# базовый вариант
from haversine import haversine
city_center_coordinates = (35.003815, -15.788289)

X_testsubm1['dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), city_center_coordinates), axis=1)


In [166]:
import pygeohash as gh
# создаем переменную - геохеш
X_testsubm1['geohash'] = X_testsubm1.apply(lambda x: gh.encode(x['X'], x['Y'], precision=6), axis=1) #лучший результат с 6 знаками
# выводим первые 5 наблюдений

In [167]:
geohash_center = gh.encode(35.003815, -15.788289, precision=6)

# преобразовываем геохеш "центра" во множество
geohash_center_set = set(geohash_center)
# создаем переменную - количество совпадающих символов
# (учитываем повторяющиеся символы)
X_testsubm1['match'] = X_testsubm1['geohash'].apply(lambda x: sum([let1 == let2 for let1, let2 in zip(geohash_center, x)]))
# создаем переменную - количество совпадающих символов
# (не учитываем повторяющиеся символы)
X_testsubm1['match2'] = X_testsubm1['geohash'].apply(lambda x: len(set(x) & geohash_center_set))

In [40]:
# добавим локации с подтоплением 2015 качество з хуже на сабмите!!!
#from haversine import haversine
#Zomba_city_center_coordinates = (35.326827, -15.386321)
#Chikwawa_city_center_coordinates = (34.791215, -16.027131)
#Phalombe_city_center_coordinates = (35.648067, -15.806557)
#Nsanje_city_center_coordinates = (35.261946, -16.923236)
#Mangochi_city_center_coordinates = (35.260613, -14.480508)
#LakeChilwa_city_center_coordinates = (35.657501, -15.389474)
#LakeMalombe_city_center_coordinates = (35.244141, -14.666633)

#X_testsubm1['Zomba_dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), Zomba_city_center_coordinates), axis=1)
#X_testsubm1['Chikwawa_dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), Chikwawa_city_center_coordinates), axis=1)
#X_testsubm1['Phalombe_dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), Phalombe_city_center_coordinates), axis=1)
#X_testsubm1['Nsanje_dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), Nsanje_city_center_coordinates), axis=1)
#X_testsubm1['Mangochi_dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), Mangochi_city_center_coordinates), axis=1)
#X_testsubm1['LakeChilwa_dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), LakeChilwa_city_center_coordinates), axis=1)
#X_testsubm1['LakeMalombe_dist_center'] = X_testsubm1.apply(lambda row: haversine((row['X'], row['Y']), LakeMalombe_city_center_coordinates), axis=1)

In [181]:
#Падает качество
#Расстояние до реки Шир ЮГ реки в виде вектора
#import math
#import numpy as np

#def shortest_distance(x1, y1, a, b, c):    
#    d = abs((a * x1 + b * y1 + c)) / (math.sqrt(a * a + b * b)) 
#    return d

#closest = []
#x = (34.745636, -15.878130)
#y = (35.149384, -16.545380)
#coef = np.polyfit(x, y, 1)
#A = coef[0]
#B = coef[1]
#C = A*x[0] + B*x[1]



#X_testsubm1['dist_river_Sheer_s'] = X_testsubm1.apply(lambda row: shortest_distance(row['X'], row['Y'], A, B, C), axis=1)


In [182]:
#Расстояние до реки Шир СЕВЕР реки в виде вектора
#import math
#import numpy as np

#def shortest_distance(x1, y1, a, b, c):    
#    d = abs((a * x1 + b * y1 + c)) / (math.sqrt(a * a + b * b)) 
#    return d

#closest = []
#x = (35.293579, -15.878130)
#y = (34.730530, -15.732779)
#coef = np.polyfit(x, y, 1)
#A = coef[0]
#B = coef[1]
#C = A*x[0] + B*x[1]



#X_testsubm1['dist_river_Sheer_n'] = X_testsubm1.apply(lambda row: shortest_distance(row['X'], row['Y'], A, B, C), axis=1)

In [183]:
#Расстояние до реки RUO реки в виде вектора
#import math
#import numpy as np

#def shortest_distance(x1, y1, a, b, c):    
#    d = abs((a * x1 + b * y1 + c)) / (math.sqrt(a * a + b * b)) 
#    return d

#closest = []
#x = (35.620422, -16.114431)
#y = (35.191956, -16.445305)
#coef = np.polyfit(x, y, 1)
#A = coef[0]
#B = coef[1]
#C = A*x[0] + B*x[1]



#X_testsubm1['dist_river_Ruo'] = X_testsubm1.apply(lambda row: shortest_distance(row['X'], row['Y'], A, B, C), axis=1)

In [102]:
#X_testsubm1  = X_testsubm1.drop(['X','Y'], axis=1) падает качество оставляем координаты

In [168]:
y_trainfull = trainfull1['target_2015'].copy()

In [169]:
X_trainfullsubm = trainfull1.drop('target_2015', axis=1)
X_testfullsubm = X_testsubm1.copy()

In [170]:
X_testfullsubm = X_testfullsubm.drop('target_2015', axis=1)

In [132]:
# импутируем NaNs 
X_trainfullsubm = X_trainfullsubm.fillna(-999)
X_testfullsubm = X_testfullsubm.fillna(-999)

In [171]:
# Label Encoding категориальных признаков. 
# Mы можем выполнить Label Encoding как до так и после разбиения на обучающую и тестовую выборки (до перекрестной проверки).

#for f in X_trainfullsubm.columns:
#    if X_trainfullsubm[f].dtype=='object' or X_testfullsubm[f].dtype=='object': 
#        lbl = preprocessing.LabelEncoder()
#        lbl.fit(list(X_trainfullsubm[f].values) + list(X_testfullsubm[f].values))
#        X_trainfullsubm[f] = lbl.transform(list(X_trainfullsubm[f].values))
#        X_testfullsubm[f] = lbl.transform(list(X_testfullsubm[f].values))

In [ ]:
# импортируем класс TargetEncoder из пакета category_encoders
from category_encoders import TargetEncoder
# создаем экземпляр класса TargetEncoder (модель)
# для обучающей выборки
target_enc = TargetEncoder(cols=['geohash', 
                                # 'LC_Type1_mode' не кодируем оставляем числами
                                ], smoothing=3, min_samples_leaf=1)
# обучаем модель, т.е. создаем таблицу, в соответствии с которой
# категориям предиктора в обучающей выборке будут сопоставлены
# сглаженные средние значения зависимой переменной
target_enc.fit(X_trainfullsubm, y_trainfull)
# применяем модель к обучающей выборке, категории предиктора
# в обучающей выборке заменяются на сглаженные средние значения зависимой
# переменной
target_encoded_train = target_enc.transform(X_trainfullsubm, y_trainfull)

# создаем экземпляр класса TargetEncoder (модель)
# для тестовой выборки
target_enc_test = TargetEncoder(cols=['geohash',
                                      #'LC_Type1_mode' оставляем числами
                                     ], smoothing=False)
# обучаем модель, т.е. создаем таблицу, в соответствии с которой
# категориям предиктора в тестовой выборке будут сопоставлены
# обычные средние значения зависимой переменной в этих категориях,
# вычисленные на обучающей выборке
target_enc_test.fit(X_trainfullsubm, y_trainfull)
# применяем модель к тестовой выборке,
# категории предиктора в тестовой выборке заменяются на обычные
# средние значения зависимой переменной в этих категориях,
# вычисленные на обучающей выборке
target_encoded_test = target_enc_test.transform(X_testfullsubm)

In [48]:
# упало качество cдобавлением кластеров
#from sklearn.cluster import KMeans
#model = KMeans(n_clusters=50)
#X_trainfullsubm ['cluster'] = model.fit_predict(X_trainfullsubm)
#X_testfullsubm ['cluster'] = model.fit_predict(X_testfullsubm)

# Modeling

In [57]:
import lightgbm as lgb  
from lightgbm import LGBMClassifier
import pickle  
params = {'objective': 'regression', 
                                       'num_leaves': 7, 
                                       'learning_rate': 0.01, 
                                       'n_estimators' : 15000,
                                       'max_bin' : 200, 
                                       'bagging_fraction': 0.75,
                                       'bagging_freq' : 5, 
                                       'bagging_seed' : 7,
                                       'feature_fraction' : 0.2, # 'was 0.2'
                                       'feature_fraction_seed' : 7,
                                       'verbose' : -1,
         }

In [58]:
trn_data = lgb.Dataset(X_trainfullsubm, label=y_trainfull)

#lgb_eval = lgb.Dataset(X_test, y_test, reference=trn_data) 
  
gbm = lgb.train(params, trn_data,  num_boost_round=3000) 

In [172]:
#лучший результат
import catboost
from sklearn.model_selection import KFold
from catboost import Pool, CatBoostClassifier, CatBoostRegressor
from catboost import MetricVisualizer
import matplotlib
import seaborn as sns
%matplotlib inline #для статики
%matplotlib widget #для динамики


UsageError: unrecognized arguments: #для статики


In [53]:
#падает качество label encoding better
#categorical_features_indices = np.where(X_trainfullsubm.dtypes == 'object')[0]
#categorical_features_indices

array([27], dtype=int64)

In [174]:


#Best
model = CatBoostRegressor(
    eval_metric='RMSE',
    iterations=9050,  
    learning_rate=0.004, 
    depth = 12, #11
    random_seed=42,
    loss_function='RMSE',
    #random_strength= 0.1,
   # bagging_temperature=0.1,
    #l2_leaf_reg= 30, 
    use_best_model = True, 
    #logging_level='Silent'
    task_type="GPU"
)

In [175]:
model.fit(
      target_encoded_train, y_trainfull,
      eval_set=(target_encoded_train, y_trainfull), 
      #cat_features=categorical_features_indices,
      use_best_model=True,
      plot=True
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 0.2279945	test: 0.2279945	best: 0.2279945 (0)	total: 300ms	remaining: 45m 11s
1:	learn: 0.2272622	test: 0.2272622	best: 0.2272622 (1)	total: 564ms	remaining: 42m 32s
2:	learn: 0.2265258	test: 0.2265258	best: 0.2265258 (2)	total: 814ms	remaining: 40m 55s
3:	learn: 0.2257881	test: 0.2257881	best: 0.2257881 (3)	total: 1.06s	remaining: 40m 8s
4:	learn: 0.2250797	test: 0.2250797	best: 0.2250797 (4)	total: 1.32s	remaining: 39m 47s
5:	learn: 0.2243766	test: 0.2243766	best: 0.2243766 (5)	total: 1.58s	remaining: 39m 42s
6:	learn: 0.2236663	test: 0.2236663	best: 0.2236663 (6)	total: 1.83s	remaining: 39m 28s
7:	learn: 0.2229650	test: 0.2229650	best: 0.2229650 (7)	total: 2.09s	remaining: 39m 20s
8:	learn: 0.2222574	test: 0.2222574	best: 0.2222574 (8)	total: 2.34s	remaining: 39m 9s
9:	learn: 0.2215637	test: 0.2215637	best: 0.2215637 (9)	total: 2.59s	remaining: 39m
10:	learn: 0.2208636	test: 0.2208636	best: 0.2208636 (10)	total: 2.84s	remaining: 38m 55s
11:	learn: 0.2201899	test: 0.2201899

92:	learn: 0.1768060	test: 0.1768060	best: 0.1768060 (92)	total: 23.8s	remaining: 38m 11s
93:	learn: 0.1763945	test: 0.1763945	best: 0.1763945 (93)	total: 24.1s	remaining: 38m 11s
94:	learn: 0.1759818	test: 0.1759818	best: 0.1759818 (94)	total: 24.3s	remaining: 38m 11s
95:	learn: 0.1755820	test: 0.1755820	best: 0.1755820 (95)	total: 24.6s	remaining: 38m 10s
96:	learn: 0.1751854	test: 0.1751854	best: 0.1751854 (96)	total: 24.8s	remaining: 38m 10s
97:	learn: 0.1747960	test: 0.1747960	best: 0.1747960 (97)	total: 25.1s	remaining: 38m 10s
98:	learn: 0.1744154	test: 0.1744155	best: 0.1744155 (98)	total: 25.3s	remaining: 38m 9s
99:	learn: 0.1740348	test: 0.1740348	best: 0.1740348 (99)	total: 25.6s	remaining: 38m 9s
100:	learn: 0.1736574	test: 0.1736574	best: 0.1736574 (100)	total: 25.8s	remaining: 38m 9s
101:	learn: 0.1732579	test: 0.1732579	best: 0.1732579 (101)	total: 26.1s	remaining: 38m 8s
102:	learn: 0.1728553	test: 0.1728553	best: 0.1728553 (102)	total: 26.3s	remaining: 38m 8s
103:	lear

182:	learn: 0.1487624	test: 0.1487624	best: 0.1487624 (182)	total: 47s	remaining: 37m 55s
183:	learn: 0.1485107	test: 0.1485107	best: 0.1485107 (183)	total: 47.2s	remaining: 37m 55s
184:	learn: 0.1482735	test: 0.1482735	best: 0.1482735 (184)	total: 47.5s	remaining: 37m 54s
185:	learn: 0.1480464	test: 0.1480464	best: 0.1480464 (185)	total: 47.7s	remaining: 37m 54s
186:	learn: 0.1478083	test: 0.1478083	best: 0.1478083 (186)	total: 48s	remaining: 37m 54s
187:	learn: 0.1476023	test: 0.1476023	best: 0.1476023 (187)	total: 48.2s	remaining: 37m 54s
188:	learn: 0.1473977	test: 0.1473977	best: 0.1473977 (188)	total: 48.5s	remaining: 37m 53s
189:	learn: 0.1471435	test: 0.1471435	best: 0.1471435 (189)	total: 48.8s	remaining: 37m 53s
190:	learn: 0.1468970	test: 0.1468970	best: 0.1468970 (190)	total: 49s	remaining: 37m 53s
191:	learn: 0.1466541	test: 0.1466541	best: 0.1466541 (191)	total: 49.3s	remaining: 37m 52s
192:	learn: 0.1464491	test: 0.1464491	best: 0.1464491 (192)	total: 49.5s	remaining: 37

272:	learn: 0.1324222	test: 0.1324223	best: 0.1324223 (272)	total: 1m 9s	remaining: 37m 29s
273:	learn: 0.1322665	test: 0.1322665	best: 0.1322665 (273)	total: 1m 10s	remaining: 37m 29s
274:	learn: 0.1321376	test: 0.1321376	best: 0.1321376 (274)	total: 1m 10s	remaining: 37m 29s
275:	learn: 0.1320114	test: 0.1320114	best: 0.1320114 (275)	total: 1m 10s	remaining: 37m 29s
276:	learn: 0.1318599	test: 0.1318599	best: 0.1318599 (276)	total: 1m 11s	remaining: 37m 29s
277:	learn: 0.1316995	test: 0.1316995	best: 0.1316995 (277)	total: 1m 11s	remaining: 37m 28s
278:	learn: 0.1315787	test: 0.1315787	best: 0.1315787 (278)	total: 1m 11s	remaining: 37m 28s
279:	learn: 0.1314415	test: 0.1314416	best: 0.1314416 (279)	total: 1m 11s	remaining: 37m 28s
280:	learn: 0.1313196	test: 0.1313196	best: 0.1313196 (280)	total: 1m 12s	remaining: 37m 27s
281:	learn: 0.1311986	test: 0.1311986	best: 0.1311986 (281)	total: 1m 12s	remaining: 37m 27s
282:	learn: 0.1310908	test: 0.1310908	best: 0.1310908 (282)	total: 1m 1

...

8679:	learn: 0.0757226	test: 0.0757226	best: 0.0757226 (8679)	total: 27m 13s	remaining: 1m 9s
8680:	learn: 0.0757226	test: 0.0757226	best: 0.0757226 (8680)	total: 27m 13s	remaining: 1m 9s
8681:	learn: 0.0757170	test: 0.0757170	best: 0.0757170 (8681)	total: 27m 13s	remaining: 1m 9s
8682:	learn: 0.0757170	test: 0.0757170	best: 0.0757170 (8682)	total: 27m 13s	remaining: 1m 9s
8683:	learn: 0.0757170	test: 0.0757170	best: 0.0757170 (8683)	total: 27m 13s	remaining: 1m 8s
8684:	learn: 0.0757139	test: 0.0757139	best: 0.0757139 (8684)	total: 27m 14s	remaining: 1m 8s
8685:	learn: 0.0757130	test: 0.0757130	best: 0.0757130 (8685)	total: 27m 14s	remaining: 1m 8s
8686:	learn: 0.0757130	test: 0.0757130	best: 0.0757130 (8686)	total: 27m 14s	remaining: 1m 8s
8687:	learn: 0.0757121	test: 0.0757121	best: 0.0757121 (8687)	total: 27m 14s	remaining: 1m 8s
8688:	learn: 0.0757120	test: 0.0757120	best: 0.0757120 (8688)	total: 27m 14s	remaining: 1m 7s
8689:	learn: 0.0757120	test: 0.0757120	best: 0.0757120 (8688

8767:	learn: 0.0756328	test: 0.0756328	best: 0.0756328 (8766)	total: 27m 25s	remaining: 52.9s
8768:	learn: 0.0756328	test: 0.0756328	best: 0.0756328 (8768)	total: 27m 25s	remaining: 52.7s
8769:	learn: 0.0756328	test: 0.0756328	best: 0.0756328 (8769)	total: 27m 25s	remaining: 52.5s
8770:	learn: 0.0756328	test: 0.0756328	best: 0.0756328 (8769)	total: 27m 25s	remaining: 52.4s
8771:	learn: 0.0756291	test: 0.0756291	best: 0.0756291 (8771)	total: 27m 26s	remaining: 52.2s
8772:	learn: 0.0756291	test: 0.0756291	best: 0.0756291 (8772)	total: 27m 26s	remaining: 52s
8773:	learn: 0.0756291	test: 0.0756291	best: 0.0756291 (8772)	total: 27m 26s	remaining: 51.8s
8774:	learn: 0.0756291	test: 0.0756291	best: 0.0756291 (8774)	total: 27m 26s	remaining: 51.6s
8775:	learn: 0.0756239	test: 0.0756239	best: 0.0756239 (8775)	total: 27m 26s	remaining: 51.4s
8776:	learn: 0.0756231	test: 0.0756231	best: 0.0756231 (8776)	total: 27m 27s	remaining: 51.2s
8777:	learn: 0.0756231	test: 0.0756231	best: 0.0756231 (8776)	

8855:	learn: 0.0755488	test: 0.0755488	best: 0.0755488 (8855)	total: 27m 37s	remaining: 36.3s
8856:	learn: 0.0755488	test: 0.0755488	best: 0.0755488 (8856)	total: 27m 37s	remaining: 36.1s
8857:	learn: 0.0755488	test: 0.0755488	best: 0.0755488 (8857)	total: 27m 37s	remaining: 35.9s
8858:	learn: 0.0755487	test: 0.0755487	best: 0.0755487 (8858)	total: 27m 37s	remaining: 35.7s
8859:	learn: 0.0755486	test: 0.0755486	best: 0.0755486 (8859)	total: 27m 37s	remaining: 35.6s
8860:	learn: 0.0755486	test: 0.0755486	best: 0.0755486 (8859)	total: 27m 37s	remaining: 35.4s
8861:	learn: 0.0755486	test: 0.0755486	best: 0.0755486 (8861)	total: 27m 38s	remaining: 35.2s
8862:	learn: 0.0755486	test: 0.0755486	best: 0.0755486 (8861)	total: 27m 38s	remaining: 35s
8863:	learn: 0.0755467	test: 0.0755467	best: 0.0755467 (8863)	total: 27m 38s	remaining: 34.8s
8864:	learn: 0.0755457	test: 0.0755457	best: 0.0755457 (8864)	total: 27m 38s	remaining: 34.6s
8865:	learn: 0.0755396	test: 0.0755396	best: 0.0755396 (8865)	

8945:	learn: 0.0754597	test: 0.0754597	best: 0.0754597 (8945)	total: 27m 50s	remaining: 19.4s
8946:	learn: 0.0754588	test: 0.0754588	best: 0.0754588 (8946)	total: 27m 51s	remaining: 19.2s
8947:	learn: 0.0754541	test: 0.0754541	best: 0.0754541 (8947)	total: 27m 51s	remaining: 19.1s
8948:	learn: 0.0754541	test: 0.0754541	best: 0.0754541 (8948)	total: 27m 51s	remaining: 18.9s
8949:	learn: 0.0754541	test: 0.0754541	best: 0.0754541 (8948)	total: 27m 51s	remaining: 18.7s
8950:	learn: 0.0754541	test: 0.0754541	best: 0.0754541 (8948)	total: 27m 51s	remaining: 18.5s
8951:	learn: 0.0754541	test: 0.0754541	best: 0.0754541 (8948)	total: 27m 51s	remaining: 18.3s
8952:	learn: 0.0754470	test: 0.0754470	best: 0.0754470 (8952)	total: 27m 51s	remaining: 18.1s
8953:	learn: 0.0754470	test: 0.0754470	best: 0.0754470 (8953)	total: 27m 51s	remaining: 17.9s
8954:	learn: 0.0754470	test: 0.0754470	best: 0.0754470 (8953)	total: 27m 51s	remaining: 17.7s
8955:	learn: 0.0754470	test: 0.0754470	best: 0.0754470 (8955

9036:	learn: 0.0753763	test: 0.0753763	best: 0.0753763 (9036)	total: 28m 2s	remaining: 2.42s
9037:	learn: 0.0753763	test: 0.0753763	best: 0.0753763 (9036)	total: 28m 2s	remaining: 2.23s
9038:	learn: 0.0753763	test: 0.0753763	best: 0.0753763 (9036)	total: 28m 2s	remaining: 2.05s
9039:	learn: 0.0753763	test: 0.0753763	best: 0.0753763 (9039)	total: 28m 2s	remaining: 1.86s
9040:	learn: 0.0753730	test: 0.0753730	best: 0.0753730 (9040)	total: 28m 2s	remaining: 1.68s
9041:	learn: 0.0753730	test: 0.0753730	best: 0.0753730 (9041)	total: 28m 2s	remaining: 1.49s
9042:	learn: 0.0753730	test: 0.0753730	best: 0.0753730 (9041)	total: 28m 2s	remaining: 1.3s
9043:	learn: 0.0753726	test: 0.0753726	best: 0.0753726 (9043)	total: 28m 3s	remaining: 1.12s
9044:	learn: 0.0753726	test: 0.0753726	best: 0.0753726 (9044)	total: 28m 3s	remaining: 930ms
9045:	learn: 0.0753707	test: 0.0753707	best: 0.0753707 (9045)	total: 28m 3s	remaining: 744ms
9046:	learn: 0.0753707	test: 0.0753707	best: 0.0753707 (9045)	total: 28

In [176]:
import numpy as np
sample_submission = pd.read_csv("D:\Python\Zindi\Flood\SampleSubmission.csv", sep=",", index_col='Square_ID')
sample_submission['target_2019'] = model.predict(X_testfullsubm)
sample_submission.to_csv('D:\Python\Zindi\Flood\samplesubm50_catboost.csv')

# Незаконченные эксперименты с стекинг+блендинг линейных моделей с стандартизацией и нормализацией

In [56]:
# пишем функцию, которая вычисляет исходный скос и
# скос после выполненных преобразований
def diagnostics_skewness(df):
# создаем список переменных
    col_list = df.select_dtypes(include=['number']).columns
    skew_initial_list = []
    skew_pos_reciprocal_list = []
    skew_neg_reciprocal_list = []
    skew_log_list = []
    skew_corr_log_001_list = []
    skew_corr_log_01_list = []
    skew_corr_log_1_list = []
    skew_corr_log_5_list = []
    skew_cbrt_list = []
    skew_sqrt_list = []
    for i in col_list:
        a = 0.001
        df_ = df.copy()
        df_ = df_.fillna(df_[i].median())
        skew_initial = df_[i].skew()
        skew_pos_reciprocal = (1 / (df_[i].clip(0) + a)).skew()
        skew_neg_reciprocal = (-1 / (df_[i].clip(0) + a)).skew()
        skew_log = np.log(df_[i].clip(0) + a).skew()
        skew_corr_log_001 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.001).skew()  
        skew_corr_log_01 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.01).skew()
        skew_corr_log_1 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.1).skew()
        skew_corr_log_5 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.5).skew()
        skew_cbrt = np.cbrt(df_[i].abs()).skew()
        skew_sqrt = np.sqrt(df_[i].abs()).skew()
        skew_initial_list.append(skew_initial)
        skew_pos_reciprocal_list.append(skew_pos_reciprocal)
        skew_neg_reciprocal_list.append(skew_neg_reciprocal)
        skew_log_list.append(skew_log)
        skew_corr_log_001_list.append(skew_corr_log_001)
        skew_corr_log_01_list.append(skew_corr_log_01)
        skew_corr_log_1_list.append(skew_corr_log_1)
        skew_corr_log_5_list.append(skew_corr_log_5)
        skew_cbrt_list.append(skew_cbrt)
        skew_sqrt_list.append(skew_sqrt)
    result = pd.DataFrame({'Переменная': col_list,
                           'Skew_init': skew_initial_list,
                           'Skew_pos_recip': skew_pos_reciprocal_list,
                           'Skew_neg_recip': skew_neg_reciprocal_list,
                           'Skew_log': skew_log_list,
                           'Skew_adj_log (k=0.001)': skew_corr_log_001_list,
                           'Skew_adj_log (k=0.01)': skew_corr_log_01_list,
                           'Skew_adj_log (k=0.1)': skew_corr_log_1_list,
                           'Skew_adj_log (k=0.5)': skew_corr_log_5_list,
                           'Skew_cbrt': skew_cbrt_list,
                           'Skew_sqrt': skew_sqrt_list})
    result = np.round(result.sort_values(by='Skew_init', ascending=False), 3)
    cm = sns.light_palette('magenta', as_cmap=True)
    return result.style.background_gradient(cmap=cm)

In [73]:


 
Skew = diagnostics_skewness(X_trainfullsubm)
 
Skew.to_excel('D:\Python\Zindi\Flood\skew.xlsx')



In [63]:
# пишем функцию, которая вычисляет исходный скос и
# скос после выполненных преобразований
def diagnostics_kurt(df):
# создаем список переменных
    col_list = df.select_dtypes(include=['number']).columns
    kurt_initial_list = []
    kurt_pos_reciprocal_list = []
    kurt_neg_reciprocal_list = []
    kurt_log_list = []
    kurt_corr_log_001_list = []
    kurt_corr_log_01_list = []
    kurt_corr_log_1_list = []
    kurt_corr_log_5_list = []
    kurt_cbrt_list = []
    kurt_sqrt_list = []
    for i in col_list:
        a = 0.001
        df_ = df.copy()
        df_ = df_.fillna(df_[i].median())
        kurt_initial = df_[i].kurtosis()
        kurt_pos_reciprocal = (1 / (df_[i].clip(0) + a)).kurtosis()
        kurt_neg_reciprocal = (-1 / (df_[i].clip(0) + a)).kurtosis()
        kurt_log = np.log(df_[i].clip(0) + a).kurtosis()
        kurt_corr_log_001 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.001).kurtosis()  
        kurt_corr_log_01 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.01).kurtosis()
        kurt_corr_log_1 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.1).kurtosis()
        kurt_corr_log_5 = np.log(((df_[i].clip(0) + a) / df_[i].mean()) + 0.5).kurtosis()
        kurt_cbrt = np.cbrt(df_[i].abs()).kurtosis()
        kurt_sqrt = np.sqrt(df_[i].abs()).kurtosis()
        kurt_initial_list.append(kurt_initial)
        kurt_pos_reciprocal_list.append(kurt_pos_reciprocal)
        kurt_neg_reciprocal_list.append(kurt_neg_reciprocal)
        kurt_log_list.append(kurt_log)
        kurt_corr_log_001_list.append(kurt_corr_log_001)
        kurt_corr_log_01_list.append(kurt_corr_log_01)
        kurt_corr_log_1_list.append(kurt_corr_log_1)
        kurt_corr_log_5_list.append(kurt_corr_log_5)
        kurt_cbrt_list.append(kurt_cbrt)
        kurt_sqrt_list.append(kurt_sqrt)
    result = pd.DataFrame({'Переменная': col_list,
                           'kurt_init': kurt_initial_list,
                           'kurt_pos_recip': kurt_pos_reciprocal_list,
                           'kurt_neg_recip': kurt_neg_reciprocal_list,
                           'kurt_log': kurt_log_list,
                           'kurt_adj_log (k=0.001)': kurt_corr_log_001_list,
                           'kurt_adj_log (k=0.01)': kurt_corr_log_01_list,
                           'kurt_adj_log (k=0.1)': kurt_corr_log_1_list,
                           'kurt_adj_log (k=0.5)': kurt_corr_log_5_list,
                           'kurt_cbrt': kurt_cbrt_list,
                           'kurt_sqrt': kurt_sqrt_list})
    result = np.round(result.sort_values(by='kurt_init', ascending=False), 3)
    cm = sns.light_palette('magenta', as_cmap=True)
    return result.style.background_gradient(cmap=cm)

In [64]:
diagnostics_kurt(X_trainfullsubm)

In [75]:
 
Kurt = diagnostics_kurt(X_trainfullsubm)
 
Kurt.to_excel('D:\Python\Zindi\Flood\kurt.xlsx')

In [79]:
from sklearn.preprocessing import PowerTransformer
# создаем модель экземпляр класса PowerTransformer
# и обучаем ее - вычисляем значения lambda


power = PowerTransformer(method='yeo-johnson', standardize=True).fit(X_trainfullsubm)

In [80]:
print(power.lambdas_)

[-6.14035336  7.17767687  0.5599863   1.13988877 -3.44472823 -0.85116865
 -0.86707833  0.25643643 -0.7999662  -0.89306361 -7.72626945 13.07057849
 -7.22058369  7.09754484 -1.85503894  7.84903855  8.68189824  6.29167028
 -1.05502795 -8.31058188 -5.12265146  0.44923125  1.09286444 -6.99506157
  0.71641979  0.8741554   0.90917914  3.77986325 -6.40079636  6.09997948]


In [82]:
X_trainfullsubm_t = power.transform(X_trainfullsubm)
X_testfullsubm_t = power.transform(X_testfullsubm)

In [ ]:
#Kaggle House example

In [34]:
from datetime import datetime
from sklearn.preprocessing import RobustScaler
from sklearn.model_selection import KFold, cross_val_score
from sklearn.metrics import mean_squared_error , make_scorer
from sklearn.linear_model import ElasticNetCV, LassoCV, RidgeCV
from sklearn.pipeline import make_pipeline
from sklearn.linear_model import LinearRegression

from sklearn.ensemble import GradientBoostingRegressor
from sklearn.svm import SVR
from mlxtend.regressor import StackingCVRegressor
from sklearn.linear_model import LinearRegression

from xgboost import XGBRegressor
from lightgbm import LGBMRegressor

from sklearn.ensemble import RandomForestRegressor
from sklearn.datasets import make_regression


In [113]:
kfolds = KFold(n_splits=10, shuffle=True, random_state=42)
X=X_trainfullsubm
y=y_trainfull

# model scoring and validation function
def cv_rmse(model, X=X):
    rmse = np.sqrt(-cross_val_score(model, X, y,scoring="neg_mean_squared_error",cv=kfolds))
    return (rmse)

# rmsle scoring function
def rmsle(y, y_pred):
    return np.sqrt(mean_squared_error(y, y_pred))

In [115]:
lightgbm = LGBMRegressor(objective='regression', 
                                       num_leaves=7, #was 3
                                       learning_rate=0.01, 
                                       n_estimators=15000, #8000
                                       max_bin=200, 
                                       bagging_fraction=0.75,
                                       bagging_freq=5, 
                                       bagging_seed=7,
                                       feature_fraction=0.2, # 'was 0.2'
                                       feature_fraction_seed=7,
                                       verbose=-1,
                                       )



xgboost = XGBRegressor(n_estimators=3800, #3500
    max_depth=13,
    #min_child_weight = 10,
    learning_rate=0.005, #eta = 0.005,
    subsample=0.9, #0.9
    colsample_bytree=0.4,
    random_state=2019,
    objective='reg:linear',
    tree_method='gpu_hist'  #обучимся на видюшке - скорость огонь минуты против часов
)

catboost = CatBoostRegressor(
    eval_metric='RMSE',
    iterations=9000,  
    learning_rate=0.005, 
    depth = 9,
    random_seed=42,
    loss_function='RMSE',
    #random_strength= 0.1,
   # bagging_temperature=0.1,
    #l2_leaf_reg= 30, 
    use_best_model = True, 
    #logging_level='Silent'
    task_type="GPU"
)


# setup models hyperparameters using a pipline
# The purpose of the pipeline is to assemble several steps that can be cross-validated together, while setting different parameters.
# This is a range of values that the model considers each time in runs a CV
e_alphas = [0.0001, 0.0002, 0.0003, 0.0004, 0.0005, 0.0006, 0.0007]
e_l1ratio = [0.8, 0.85, 0.9, 0.95, 0.99, 1]
alphas_alt = [14.5, 14.6, 14.7, 14.8, 14.9, 15, 15.1, 15.2, 15.3, 15.4, 15.5]
alphas2 = [5e-05, 0.0001, 0.0002, 0.0003, 0.0004, 0.0005, 0.0006, 0.0007, 0.0008]




# Kernel Ridge Regression : made robust to outliers
ridge = make_pipeline(RobustScaler(), RidgeCV(alphas=alphas_alt, cv=kfolds))

# LASSO Regression : made robust to outliers
lasso = make_pipeline(RobustScaler(), LassoCV(max_iter=1e7, 
                    alphas=alphas2,random_state=42, cv=kfolds))

# Elastic Net Regression : made robust to outliers
elasticnet = make_pipeline(RobustScaler(), ElasticNetCV(max_iter=1e7, 
                         alphas=e_alphas, cv=kfolds, l1_ratio=e_l1ratio))

RF = RandomForestRegressor(max_depth=15, random_state=0)


stack_gen = StackingCVRegressor(regressors=(ridge, lasso, elasticnet, lightgbm, xgboost, catboost),
                                meta_regressor=RF,
                                use_features_in_secondary=True)


svr = make_pipeline(RobustScaler(), SVR(C= 20, epsilon= 0.008, gamma=0.0003))

# store models, scores and prediction values 
models = {'Ridge': ridge,
          'Lasso': lasso, 
          'ElasticNet': elasticnet,
          'lightgbm': lightgbm,
          'Svd': svr,
          'xgboost': xgboost,
          'catboost': catboost,
         'RF' : RF}
predictions = {}
scores = {}

In [117]:
for name, model in models.items():
    
    model.fit(X, y)
    predictions[name] = np.expm1(model.predict(X))
    
    score = cv_rmse(model, X=X)
    scores[name] = (score.mean(), score.std())

[20:26:52] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[20:33:21] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[20:39:30] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[20:45:34] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[20:51:36] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[20:57:17] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[21:03:00] WARNI

In [118]:
# get the performance of each model on training data(validation set)
print('---- Score with CV_RMSLE-----')
score = cv_rmse(ridge)
print("Ridge score: {:.4f} ({:.4f})\n".format(score.mean(), score.std()))

score = cv_rmse(lasso)
print("Lasso score: {:.4f} ({:.4f})\n".format(score.mean(), score.std()))

score = cv_rmse(elasticnet)
print("ElasticNet score: {:.4f} ({:.4f})\n".format(score.mean(), score.std()))

score = cv_rmse(lightgbm)
print("lightgbm score: {:.4f} ({:.4f})\n".format(score.mean(), score.std()))

score = cv_rmse(svr)
print("SVR: {:.4f} ({:.4f})".format(score.mean(), score.std()))
# scores['svr'] = (score.mean(), score.std())

score = cv_rmse(xgboost)
print("xgboost score: {:.4f} ({:.4f})\n".format(score.mean(), score.std()))

score = cv_rmse(catboost)
print("catboost score: {:.4f} ({:.4f})\n".format(score.mean(), score.std()))

#Fit the training data X, y
print('----START Fit----',datetime.now())
print('Elasticnet')
elastic_model = elasticnet.fit(X, y)
print('Lasso')
lasso_model = lasso.fit(X, y)
print('Ridge')
ridge_model = ridge.fit(X, y)
print('lightgbm')
lgb_model_full_data = lightgbm.fit(X, y)
print('Svr')
svr_model_full_data = svr.fit(X, y)

print('xgboost')
xgb_model_full_data = xgboost.fit(X, y)
print('catboost')
cat_model_full_data = catboost.fit(X, y)

print('stack_gen')
stack_gen_model = stack_gen.fit(np.array(X), np.array(y))

---- Score with CV_RMSLE-----
Ridge score: 0.2128 (0.0067)

Lasso score: 0.2128 (0.0067)

ElasticNet score: 0.2129 (0.0067)

lightgbm score: 0.1051 (0.0025)

SVR: 0.2277 (0.0082)
[21:36:25] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[21:43:23] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[21:49:52] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[21:55:59] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[22:02:21] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[

In [119]:
def blend_models_predict(X):
    return ((0.1  * elastic_model.predict(X)) + \
            (0.1 * lasso_model.predict(X)) + \
            (0.1 * ridge_model.predict(X)) + \
            (0.2 * lgb_model_full_data.predict(X)) + \
            (0.03 * svr_model_full_data.predict(X)) + \
            (0.2 * xgb_model_full_data.predict(X)) + \
            (0.2 * cat_model_full_data.predict(X)) + \
            (0.27 * stack_gen_model.predict(np.array(X))))

In [120]:
print('RMSLE score on train data:')
print(rmsle(y, blend_models_predict(X)))

RMSLE score on train data:
0.1006752451149785


In [121]:
import numpy as np
sample_submission = pd.read_csv("D:\Python\Zindi\Flood\SampleSubmission.csv", sep=",", index_col='Square_ID')
sample_submission['target_2019'] = blend_models_predict(X_testfullsubm)
sample_submission.to_csv('D:\Python\Zindi\Flood\samplesubm22_xgboost.csv')